In [1]:
import pandas as pd

dfplus = pd.read_csv("order_details_sample.csv")
dfplus.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 204204 entries, 0 to 204203
Data columns (total 5 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   date_key    204204 non-null  object
 1   order_id    204204 non-null  int64 
 2   quantity    204204 non-null  int64 
 3   hub_id      204204 non-null  int64 
 4   product_id  204204 non-null  int64 
dtypes: int64(4), object(1)
memory usage: 7.8+ MB


In [2]:
# Recover transaction itemsets from orders DataFrame.
transactions = dfplus.groupby("order_id").product_id.unique()

order_df = transactions.reset_index()

In [3]:
print(dfplus.head())

     date_key  order_id  quantity  hub_id  product_id
0  2023-01-10   3798331         1       8          19
1  2023-01-10   3800937         1       8         128
2  2023-01-10   3800937         1       8          38
3  2023-01-10   3800937         1       8         263
4  2023-01-10   3798331         3       8         839


In [4]:
print(order_df.head())

   order_id                               product_id
0   3181466                         [307, 2111, 277]
1   3181501                  [237, 2755, 1305, 2160]
2   3181506  [1104, 1102, 2816, 2461, 877, 878, 112]
3   3181509                                   [2630]
4   3181512                         [1157, 447, 546]


In [133]:
import pandas as pd

# Load the association rules data from the file "sequence_combine.csv"
seq8 = pd.read_csv("sequence8apriori0001.csv")
seq207 = pd.read_csv("sequence207apriori0005.csv")
df = pd.concat([seq8,seq207], ignore_index=True)
def clean_frozenset(row):
    return row.replace("frozenset({", "").replace("})", "")
df['antecedents'] = df['antecedents'].apply(clean_frozenset)
df['consequents'] = df['consequents'].apply(clean_frozenset)
# Drop the first column
df = df.drop(columns=["Unnamed: 0"])
df

# Group consequents for each unique antecedent and concatenate them into a single sequence
grouped_df = df.groupby('antecedents')['consequents'].agg(list).reset_index()
#grouped_df['consequents'] = grouped_df['consequents'].apply(lambda lst: ', '.join(map(str, lst)))

In [134]:
association_rules_df = df

In [135]:
# Function to add comma to single items in the string
def add_trailing_comma(item_list):
    items = item_list.split(', ')
    if len(items) == 1:
        return item_list + ','
    return item_list

# Apply the function to 'antecedents' and 'consequents' columns
association_rules_df['antecedents'] = association_rules_df['antecedents'].apply(add_trailing_comma)
association_rules_df['consequents'] = association_rules_df['consequents'].apply(add_trailing_comma)

# Display the modified DataFrame
association_rules_df.tail()

antecedents            consequents
9091       3269,   821, 3276, 1037, 949
9092       3276,   1037, 821, 3269, 949
9093       1037,   821, 3276, 3269, 949
9094        821,  1037, 3276, 3269, 949
9095        949,  1037, 821, 3276, 3269

In [136]:
# Convert item IDs in the association rules to strings
association_rules_df['antecedents'] = association_rules_df['antecedents'].apply(lambda x: [str(item) for item in eval(x)])
association_rules_df['consequents'] = association_rules_df['consequents'].apply(lambda x: [str(item) for item in eval(x)])

# Create a list to hold the sequences of itemsets for each transaction order
sequences = []

# Process each order's transaction
for order in order_df['product_id']:
    sequence = []
    for rule in association_rules_df.itertuples():
        antecedent, consequent = rule.antecedents, rule.consequents
        if set(antecedent).issubset(set(order)):
            sequence.extend(consequent)
    # Add remaining unique items to the sequence
    remaining_items = set(order) - set(sequence)
    sequence.extend(remaining_items)
    sequences.append(sequence)

# Print the resulting sequences
print(sequences)

[[307, 277, 2111], [2160, 1305, 2755, 237], [2816, 1104, 878, 112, 2461, 877, 1102], [2630], [546, 1157, 447], [154, 1915, 623], [1087, 3013, 2157, 1654, 1549, 1871], [3018], [256, 1180, 19, 2854, 1496, 908, 111], [883, 2102], [765, 2549], [1713, 299, 1190, 47], [1434], [393, 1003], [209, 546, 1713, 298, 46], [194, 263, 201, 1770, 2737, 3026, 19, 788, 789, 2738, 2525, 1439], [908, 103, 2556], [2592, 1270, 475, 38], [2432, 295, 810, 1004, 303, 1841, 180, 1045, 2906, 2911], [1326, 895, 502, 799], [2148], [185, 1595, 2060, 1385], [1571, 2884, 741, 2949, 197, 102, 16, 466, 3033], [2560, 2691, 19, 295, 1915, 2559], [2692, 293, 294, 295, 296, 1545, 1045, 1052], [1802, 1796, 1493, 1798], [1346, 103, 185, 908, 2237], [277, 2839, 3016, 2572, 237, 3005, 3148], [882, 895], [1345, 908], [930, 19, 2948, 2564, 24], [1669, 2437], [1912, 950, 2367], [1376, 410, 2199], [49, 19, 26, 380, 1434, 364, 604], [259, 19, 1749, 2199, 1208, 2905], [2107, 1812], [192, 1, 611, 163, 505], [448, 2113, 601, 3034, 151

In [34]:
#with open("file4.txt", "w") as output:
#   output.write(str(sequences))

In [137]:
antecedents_list = grouped_df['antecedents'].tolist()
consequents_list = grouped_df['consequents'].tolist()

In [138]:
# Combine antecedents with consequents into a single column
grouped_df['combined'] = grouped_df.apply(lambda row: [row['antecedents']] + row['consequents'], axis=1)

In [139]:
grouped_df_list = grouped_df['combined'].tolist()

# Convert the list to a new list with combined elements
grouped_list = [[', '.join(sublist)] for sublist in grouped_df_list]

# Print the new list
print(grouped_list)

[['1, 697'], ['100, 148, 160, 201, 106, 122, 148, 160, 201, 908, 1244, 1245, 1617, 1618, 1787, 1812, 160, 1244, 160, 1245, 160, 1617, 160, 1787, 160, 1812, 1244, 1245, 1617, 1245, 160, 1244, 1245, 160, 1617, 1245'], ['100, 1244, 1245'], ['100, 1245, 160, 1244, 1617, 160, 1244, 160, 1617'], ['100, 1812, 160'], ['1000, 263, 295, 296, 908, 1340, 1380, 2782, 3530, 3567'], ['1001, 933'], ['1015, 122, 201, 128, 1244, 1245, 1384, 1384, 1245'], ['1016, 201'], ['1017, 122, 128, 160, 201, 908, 1242, 1245, 1374, 1514, 1617, 1720, 106, 128, 160, 215, 1245, 1374, 1720, 2885, 2885, 215'], ['1017, 215, 2885'], ['1017, 2885, 215'], ['1019, 1991'], ['102, 106, 120, 122, 148, 160, 201, 908, 1244, 1245, 1514, 1617, 1618, 1622, 1244, 1245, 17, 103, 106, 122, 128, 160, 201, 215, 466, 1242, 1244, 1245, 1260, 1586, 1617, 1618, 1622, 1720, 1727, 1812, 2427, 2621, 2884, 2885, 2885, 103, 201, 106, 201, 215, 201, 1242, 1244, 1245'], ['102, 103, 2885'], ['102, 215, 201'], ['1020, 1751, 2851'], ['103, 106, 128, 16

In [140]:
# Convert elements to integer lists
grouped_new_list = [[int(item) for item in sublist[0].split(', ')] for sublist in grouped_list]

# Print the new list
print(grouped_new_list)

[[1, 697], [100, 148, 160, 201, 106, 122, 148, 160, 201, 908, 1244, 1245, 1617, 1618, 1787, 1812, 160, 1244, 160, 1245, 160, 1617, 160, 1787, 160, 1812, 1244, 1245, 1617, 1245, 160, 1244, 1245, 160, 1617, 1245], [100, 1244, 1245], [100, 1245, 160, 1244, 1617, 160, 1244, 160, 1617], [100, 1812, 160], [1000, 263, 295, 296, 908, 1340, 1380, 2782, 3530, 3567], [1001, 933], [1015, 122, 201, 128, 1244, 1245, 1384, 1384, 1245], [1016, 201], [1017, 122, 128, 160, 201, 908, 1242, 1245, 1374, 1514, 1617, 1720, 106, 128, 160, 215, 1245, 1374, 1720, 2885, 2885, 215], [1017, 215, 2885], [1017, 2885, 215], [1019, 1991], [102, 106, 120, 122, 148, 160, 201, 908, 1244, 1245, 1514, 1617, 1618, 1622, 1244, 1245, 17, 103, 106, 122, 128, 160, 201, 215, 466, 1242, 1244, 1245, 1260, 1586, 1617, 1618, 1622, 1720, 1727, 1812, 2427, 2621, 2884, 2885, 2885, 103, 201, 106, 201, 215, 201, 1242, 1244, 1245], [102, 103, 2885], [102, 215, 201], [1020, 1751, 2851], [103, 106, 128, 160, 185, 201, 908, 1242, 1244, 1245,

In [141]:
new_sequences = sequences + grouped_new_list

In [25]:
'''
# Split data into training and testing sets
X_list = [seq[:-1] for seq in sequences]  # Input sequences (exclude last item)
y_list = [seq[1:] for seq in sequences]   # Output sequences (exclude first item)
grouped_X_list = [seq[:-1] for seq in grouped_new_list]
grouped_y_list = [seq[1:] for seq in grouped_new_list]

print(X_list)
print(y_list)
print(grouped_X_list)
print(grouped_y_list)

[[307, 277], [2160, 1305, 2755], [2816, 1104, 878, 112, 2461, 877], [], [546, 1157], [154, 1915], [1087, 3013, 2157, 1654, 1549], [], [256, 1180, 19, 2854, 1496, 908], [883], [765], [1713, 299, 1190], [], [393], [209, 546, 1713, 298], [194, 263, 201, 1770, 2737, 3026, 19, 788, 789, 2738, 2525], [908, 103], [2592, 1270, 475], [2432, 295, 810, 1004, 303, 1841, 180, 1045, 2906], [1326, 895, 502], [], [185, 1595, 2060], [1571, 2884, 741, 2949, 197, 102, 16, 466], [2560, 2691, 19, 295, 1915], [2692, 293, 294, 295, 296, 1545, 1045], [1802, 1796, 1493], [1346, 103, 185, 908], [277, 2839, 3016, 2572, 237, 3005], [882], [1345], [930, 19, 2948, 2564], [1669], [1912, 950], [1376, 410], [49, 19, 26, 380, 1434, 364], [259, 19, 1749, 2199, 1208], [2107], [192, 1, 611, 163], [448, 2113, 601, 3034], [2432, 1665, 136, 2427, 1581], [185, 21, 190], [294, 1542, 296, 201, 1384, 1675, 908, 17, 1715, 1336], [788, 950, 1366, 237, 2762, 1996], [296], [1756], [293, 2677], [185, 19], [], [2723, 243, 454, 1111, 2

In [26]:
'''
# Convert the list to a new list with quote characters per sublist
X_new_list = [[', '.join(map(str, sublist))] for sublist in X_list]
y_new_list = [[', '.join(map(str, sublist))] for sublist in y_list]
grouped_X_new_list = [[', '.join(map(str, sublist))] for sublist in grouped_list]
grouped_y_new_list = [[', '.join(map(str, sublist))] for sublist in grouped_list]

# Print the new list
print(X_new_list)
print(y_new_list)
print(grouped_X_new_list)
print(grouped_y_new_list)

[['307, 277'], ['2160, 1305, 2755'], ['2816, 1104, 878, 112, 2461, 877'], [''], ['546, 1157'], ['154, 1915'], ['1087, 3013, 2157, 1654, 1549'], [''], ['256, 1180, 19, 2854, 1496, 908'], ['883'], ['765'], ['1713, 299, 1190'], [''], ['393'], ['209, 546, 1713, 298'], ['194, 263, 201, 1770, 2737, 3026, 19, 788, 789, 2738, 2525'], ['908, 103'], ['2592, 1270, 475'], ['2432, 295, 810, 1004, 303, 1841, 180, 1045, 2906'], ['1326, 895, 502'], [''], ['185, 1595, 2060'], ['1571, 2884, 741, 2949, 197, 102, 16, 466'], ['2560, 2691, 19, 295, 1915'], ['2692, 293, 294, 295, 296, 1545, 1045'], ['1802, 1796, 1493'], ['1346, 103, 185, 908'], ['277, 2839, 3016, 2572, 237, 3005'], ['882'], ['1345'], ['930, 19, 2948, 2564'], ['1669'], ['1912, 950'], ['1376, 410'], ['49, 19, 26, 380, 1434, 364'], ['259, 19, 1749, 2199, 1208'], ['2107'], ['192, 1, 611, 163'], ['448, 2113, 601, 3034'], ['2432, 1665, 136, 2427, 1581'], ['185, 21, 190'], ['294, 1542, 296, 201, 1384, 1675, 908, 17, 1715, 1336'], ['788, 950, 1366, 

In [27]:
#new_sequences = X_new_list + y_new_list + grouped_X_new_list + grouped_y_new_list

In [142]:
len(new_sequences)

41954

In [143]:
import numpy as np
from sklearn.model_selection import train_test_split

# Convert sequences to one-hot encoded vectors
unique_items = list(set(item for sequence in new_sequences for item in sequence))
item_to_index = {item: index for index, item in enumerate(unique_items)}

def one_hot_encode_sequence(sequence):
    return [item_to_index[item] for item in sequence]

encoded_sequences = [one_hot_encode_sequence(sequence) for sequence in new_sequences]

# Split data into training and testing sets
X = [seq[:-1] for seq in encoded_sequences]  # Input sequences (exclude last item)
y = [seq[1:] for seq in encoded_sequences]   # Output sequences (exclude first item)

In [144]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [134]:
# Split data into training and testing sets
#X = [seq[:-1] for seq in encoded_sequences]  # Input sequences (exclude last item)
#y = [seq[1:] for seq in encoded_sequences]   # Output sequences (exclude first item)

In [145]:
X_test_pad_new = X_test_pad
X_test_new = X_test

In [146]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.01, random_state=42)

In [147]:
import tensorflow as tf
# Pad sequences to a fixed length (length of the longest sequence)
max_sequence_length = max(len(seq) for seq in sequences)

X_train_pad = tf.keras.preprocessing.sequence.pad_sequences(X_train, maxlen=max_sequence_length)
X_test_pad = tf.keras.preprocessing.sequence.pad_sequences(X_test, maxlen=max_sequence_length)
y_train_pad = tf.keras.preprocessing.sequence.pad_sequences(y_train, maxlen=max_sequence_length)
y_test_pad = tf.keras.preprocessing.sequence.pad_sequences(y_test, maxlen=max_sequence_length)

In [148]:
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import GRU, Dense, Embedding

# Verify GPU availability
print("GPU Available:", tf.config.list_physical_devices('GPU'))

# Pad sequences to a fixed length (length of the longest sequence)
# max_sequence_length = max(len(seq) for seq in sequences)

#X_train_pad = tf.keras.preprocessing.sequence.pad_sequences(X_train, maxlen=max_sequence_length)
#X_test_pad = tf.keras.preprocessing.sequence.pad_sequences(X_test, maxlen=max_sequence_length)
#y_train_pad = tf.keras.preprocessing.sequence.pad_sequences(y_train, maxlen=max_sequence_length)
#y_test_pad = tf.keras.preprocessing.sequence.pad_sequences(y_test, maxlen=max_sequence_length)

# Build the GRU model
embedding_dim = 50
vocab_size = len(unique_items)

model = tf.keras.Sequential([
    tf.keras.layers.Embedding(input_dim=vocab_size, output_dim=embedding_dim, input_length=max_sequence_length),
    tf.keras.layers.GRU(units=128, return_sequences=True),
    tf.keras.layers.Dense(vocab_size, activation='softmax')
])

# Compile the model
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Move the data and model to GPU (if available)
with tf.device('/GPU:0'):
    model.fit(X_train_pad, y_train_pad, epochs=10, batch_size=32)

GPU Available: [PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]
Epoch 1/10


2023-07-31 01:08:03.550481: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.
2023-07-31 01:08:03.719922: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


   1/1298 [..............................] - ETA: 42:38 - loss: 8.1956 - accuracy: 0.0000e+00

2023-07-31 01:08:04.117397: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


1298/1298 [==============================] - 42s 31ms/step - loss: 0.7269 - accuracy: 0.9314
Epoch 2/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.4762 - accuracy: 0.9339
Epoch 3/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.4556 - accuracy: 0.9344
Epoch 4/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.4391 - accuracy: 0.9351
Epoch 5/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.4232 - accuracy: 0.9358
Epoch 6/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.4099 - accuracy: 0.9366
Epoch 7/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.3986 - accuracy: 0.9371
Epoch 8/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.3889 - accuracy: 0.9377
Epoch 9/10
1298/1298 [==============================] - 39s 30ms/step - loss: 0.3803 - accuracy: 0.9382
Epoch 10/10
1298/1298 [==============================] - 39s 30ms/step - lo

In [149]:
loss = model.evaluate(X_test_pad, np.expand_dims(y_test_pad, axis=-1))
print("Test Loss:", loss)

2023-07-31 01:14:57.330080: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.
2023-07-31 01:14:57.413363: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


14/14 [==============================] - 1s 45ms/step - loss: 0.3949 - accuracy: 0.9412
Test Loss: [0.3949038088321686, 0.9411787390708923]


In [150]:
model.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_3 (Embedding)     (None, 61, 50)            179750    
                                                                 
 gru_3 (GRU)                 (None, 61, 128)           69120     
                                                                 
 dense_2 (Dense)             (None, 61, 3595)          463755    
                                                                 
Total params: 712625 (2.72 MB)
Trainable params: 712625 (2.72 MB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [151]:
model.save("model_aa.h5")

/Users/fahmi/tensorflow-test/env/lib/python3.8/site-packages/keras/src/engine/training.py:3000: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


In [55]:
X_test_pad_new

array([[   0,    0,    0, ...,  184, 1721, 1243],
       [   0,    0,    0, ...,    0,    0,  882],
       [   0,    0,    0, ...,  916, 3386, 1948],
       ...,
       [   0,    0,    0, ...,  277,  121, 1786],
       [   0,    0,    0, ..., 1271, 3354, 2691],
       [   0,    0,    0, ..., 2352, 2154, 1524]], dtype=int32)

In [56]:
item_to_index

{1: 0,
 2: 1,
 3: 2,
 4: 3,
 5: 4,
 6: 5,
 7: 6,
 8: 7,
 9: 8,
 10: 9,
 11: 10,
 12: 11,
 13: 12,
 14: 13,
 15: 14,
 16: 15,
 17: 16,
 18: 17,
 19: 18,
 20: 19,
 21: 20,
 22: 21,
 23: 22,
 24: 23,
 25: 24,
 26: 25,
 27: 26,
 28: 27,
 29: 28,
 30: 29,
 31: 30,
 32: 31,
 33: 32,
 34: 33,
 35: 34,
 36: 35,
 37: 36,
 38: 37,
 39: 38,
 40: 39,
 41: 40,
 42: 41,
 43: 42,
 44: 43,
 45: 44,
 46: 45,
 47: 46,
 48: 47,
 49: 48,
 50: 49,
 51: 50,
 52: 51,
 53: 52,
 54: 53,
 55: 54,
 56: 55,
 57: 56,
 58: 57,
 59: 58,
 60: 59,
 61: 60,
 62: 61,
 63: 62,
 64: 63,
 65: 64,
 66: 65,
 67: 66,
 68: 67,
 69: 68,
 70: 69,
 71: 70,
 72: 71,
 73: 72,
 74: 73,
 75: 74,
 76: 75,
 77: 76,
 78: 77,
 79: 78,
 80: 79,
 81: 80,
 82: 81,
 83: 82,
 84: 83,
 85: 84,
 86: 85,
 87: 86,
 88: 87,
 89: 88,
 90: 89,
 91: 90,
 92: 91,
 93: 92,
 94: 93,
 95: 94,
 96: 95,
 97: 96,
 98: 97,
 99: 98,
 100: 99,
 101: 100,
 102: 101,
 103: 102,
 104: 103,
 105: 104,
 106: 105,
 107: 106,
 108: 107,
 109: 108,
 110: 109,
 111: 11

In [152]:
# Example: Make predictions for the first 5 sequences in the test set
predictions = model.predict(np.array(X_test_pad_new[:50]))

# Convert predictions to their original form (product IDs)
for i, (sequence, pred) in enumerate(zip(X_test_new[:50], predictions)):
    next_item_index = np.argmax(pred[-1])  # Get the index of the next item with the highest probability
    next_item = unique_items[next_item_index]
    input_sequence = [unique_items[item_index] for item_index in sequence]
    print(f"Sequence {i + 1}: Input Sequence: {input_sequence}, Predicted Next Item: {next_item}")

2/2 [==============================] - 0s 63ms/step


2023-07-31 01:15:25.475379: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.
2023-07-31 01:15:25.512138: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


Sequence 1: Input Sequence: [1538, 3427, 39, 874, 590, 627, 793], Predicted Next Item: 1245
Sequence 2: Input Sequence: [2194, 246, 574, 1725], Predicted Next Item: 263
Sequence 3: Input Sequence: [2615, 1436, 602, 1756], Predicted Next Item: 639
Sequence 4: Input Sequence: [1434], Predicted Next Item: 1999
Sequence 5: Input Sequence: [1150, 2634, 134], Predicted Next Item: 2620
Sequence 6: Input Sequence: [160, 2210, 2405, 1639, 1965, 2578, 3123, 2427, 3251, 950, 2199, 1723], Predicted Next Item: 1327
Sequence 7: Input Sequence: [353, 350, 166, 504, 1995, 2766], Predicted Next Item: 190
Sequence 8: Input Sequence: [1253, 567, 1003, 2683, 2011], Predicted Next Item: 908
Sequence 9: Input Sequence: [1617, 1244, 1245, 908, 1618, 148, 160], Predicted Next Item: 835
Sequence 10: Input Sequence: [128, 1514, 1356, 365, 1751, 1080, 185, 1242, 2523], Predicted Next Item: 1245
Sequence 11: Input Sequence: [352, 1717, 1720, 170], Predicted Next Item: 190
Sequence 12: Input Sequence: [601, 3172, 

In [153]:
# Example: Make predictions for the first 5 sequences in the test set
predictions = model.predict(np.array(X_test_pad_new[:50]))

# Convert predictions to their original form (product IDs)
for i, (sequence, pred) in enumerate(zip(X_test_new[:50], predictions), 1):
    next_item_index = np.argmax(pred[-1])  # Get the index of the next item with the highest probability
    next_item = unique_items[next_item_index]  # Convert the index to the corresponding product ID
    input_sequence = [unique_items[item_index] for item_index in sequence]  # Convert sequence indices to product IDs
    print(f"Sequence {i}: Input Sequence: {input_sequence}, Predicted Next Item: {next_item}")

2/2 [==============================] - 0s 48ms/step
Sequence 1: Input Sequence: [1538, 3427, 39, 874, 590, 627, 793], Predicted Next Item: 1245
Sequence 2: Input Sequence: [2194, 246, 574, 1725], Predicted Next Item: 263
Sequence 3: Input Sequence: [2615, 1436, 602, 1756], Predicted Next Item: 639
Sequence 4: Input Sequence: [1434], Predicted Next Item: 1999
Sequence 5: Input Sequence: [1150, 2634, 134], Predicted Next Item: 2620
Sequence 6: Input Sequence: [160, 2210, 2405, 1639, 1965, 2578, 3123, 2427, 3251, 950, 2199, 1723], Predicted Next Item: 1327
Sequence 7: Input Sequence: [353, 350, 166, 504, 1995, 2766], Predicted Next Item: 190
Sequence 8: Input Sequence: [1253, 567, 1003, 2683, 2011], Predicted Next Item: 908
Sequence 9: Input Sequence: [1617, 1244, 1245, 908, 1618, 148, 160], Predicted Next Item: 835
Sequence 10: Input Sequence: [128, 1514, 1356, 365, 1751, 1080, 185, 1242, 2523], Predicted Next Item: 1245
Sequence 11: Input Sequence: [352, 1717, 1720, 170], Predicted Next

In [30]:
# Assuming you have already imported the required libraries and defined unique_items.
import numpy as np

# Example: Make predictions for the first 50 sequences in the test set
predictions = model.predict(np.array(X_test_pad_new[:50]))

# Convert predictions to their original form (product IDs) and calculate accuracy
correct_predictions = 0
total_predictions = 0

for i, (sequence, pred) in enumerate(zip(X_test_new[:50], predictions), 1):
    next_item_index = np.argmax(pred[-1])  # Get the index of the next item with the highest probability
    next_item = unique_items[next_item_index]  # Convert the index to the corresponding product ID
    input_sequence = [unique_items[item_index] for item_index in sequence]  # Convert sequence indices to product IDs
    print(f"Sequence {i}: Input Sequence: {input_sequence}, Predicted Next Item: {next_item}")

    # Get the true next item from the test set
    true_next_item_index = sequence[-1]
    true_next_item = unique_items[true_next_item_index]

    # Compare the predicted next item with the true next item
    if next_item == true_next_item:
        correct_predictions += 1

    total_predictions += 1

# Calculate accuracy
accuracy = correct_predictions / total_predictions
print(f"Model Accuracy: {accuracy * 100:.2f}%")

2/2 [==============================] - 0s 7ms/step
Sequence 1: Input Sequence: [160, 1089, 2428], Predicted Next Item: 1611
Sequence 2: Input Sequence: [2851, 2885, 1611, 908, 627, 1494, 1527], Predicted Next Item: 1242
Sequence 3: Input Sequence: [2, 349], Predicted Next Item: 1637
Sequence 4: Input Sequence: [3027, 2249, 890, 1915], Predicted Next Item: 908
Sequence 5: Input Sequence: [641, 258, 1411, 2658, 406, 9], Predicted Next Item: 2683
Sequence 6: Input Sequence: [1376, 3456, 1762, 2226, 3061], Predicted Next Item: 263
Sequence 7: Input Sequence: [3567], Predicted Next Item: 19
Sequence 8: Input Sequence: [1715], Predicted Next Item: 1716
Sequence 9: Input Sequence: [], Predicted Next Item: 1


IndexError: ignored

In [154]:
# Example: Make predictions for the first 5 sequences in the test set
predictions = model.predict(np.array(X_test_pad_new[:50]))

# Convert predictions to their original form (product IDs)
for i, (sequence, pred) in enumerate(zip(X_test_new[:50], predictions)):
    next_item_index = np.argmax(pred[-1])  # Get the index of the next item with the highest probability
    next_item = unique_items[next_item_index]
    input_sequence = [unique_items[item_index] for item_index in sequence]
    print(f"Sequence {i + 1}: Input Sequence: {input_sequence}, Predicted Next Item: {next_item}")


2/2 [==============================] - 0s 36ms/step
Sequence 1: Input Sequence: [1538, 3427, 39, 874, 590, 627, 793], Predicted Next Item: 1245
Sequence 2: Input Sequence: [2194, 246, 574, 1725], Predicted Next Item: 263
Sequence 3: Input Sequence: [2615, 1436, 602, 1756], Predicted Next Item: 639
Sequence 4: Input Sequence: [1434], Predicted Next Item: 1999
Sequence 5: Input Sequence: [1150, 2634, 134], Predicted Next Item: 2620
Sequence 6: Input Sequence: [160, 2210, 2405, 1639, 1965, 2578, 3123, 2427, 3251, 950, 2199, 1723], Predicted Next Item: 1327
Sequence 7: Input Sequence: [353, 350, 166, 504, 1995, 2766], Predicted Next Item: 190
Sequence 8: Input Sequence: [1253, 567, 1003, 2683, 2011], Predicted Next Item: 908
Sequence 9: Input Sequence: [1617, 1244, 1245, 908, 1618, 148, 160], Predicted Next Item: 835
Sequence 10: Input Sequence: [128, 1514, 1356, 365, 1751, 1080, 185, 1242, 2523], Predicted Next Item: 1245
Sequence 11: Input Sequence: [352, 1717, 1720, 170], Predicted Next

In [161]:
item_to_index

{1: 0,
 2: 1,
 3: 2,
 4: 3,
 5: 4,
 6: 5,
 7: 6,
 8: 7,
 9: 8,
 10: 9,
 11: 10,
 12: 11,
 13: 12,
 14: 13,
 15: 14,
 16: 15,
 17: 16,
 18: 17,
 19: 18,
 20: 19,
 21: 20,
 22: 21,
 23: 22,
 24: 23,
 25: 24,
 26: 25,
 27: 26,
 28: 27,
 29: 28,
 30: 29,
 31: 30,
 32: 31,
 33: 32,
 34: 33,
 35: 34,
 36: 35,
 37: 36,
 38: 37,
 39: 38,
 40: 39,
 41: 40,
 42: 41,
 43: 42,
 44: 43,
 45: 44,
 46: 45,
 47: 46,
 48: 47,
 49: 48,
 50: 49,
 51: 50,
 52: 51,
 53: 52,
 54: 53,
 55: 54,
 56: 55,
 57: 56,
 58: 57,
 59: 58,
 60: 59,
 61: 60,
 62: 61,
 63: 62,
 64: 63,
 65: 64,
 66: 65,
 67: 66,
 68: 67,
 69: 68,
 70: 69,
 71: 70,
 72: 71,
 73: 72,
 74: 73,
 75: 74,
 76: 75,
 77: 76,
 78: 77,
 79: 78,
 80: 79,
 81: 80,
 82: 81,
 83: 82,
 84: 83,
 85: 84,
 86: 85,
 87: 86,
 88: 87,
 89: 88,
 90: 89,
 91: 90,
 92: 91,
 93: 92,
 94: 93,
 95: 94,
 96: 95,
 97: 96,
 98: 97,
 99: 98,
 100: 99,
 101: 100,
 102: 101,
 103: 102,
 104: 103,
 105: 104,
 106: 105,
 107: 106,
 108: 107,
 109: 108,
 110: 109,
 111: 11

In [324]:
# Define a function to prepare the input sequence
def prepare_input_sequence(input_product_ids, max_length):
    # Convert input product IDs to integers and find their corresponding indices in the item_to_index dictionary
    input_indices = [item_to_index[int(item_id)] for item_id in input_product_ids]

    # Pad or truncate the sequence to the maximum length
    if len(input_indices) < max_length:
        padded_sequence = [0] * (max_length - len(input_indices)) + input_indices 
    elif len(input_indices) > max_length:
        padded_sequence = input_indices[:max_length]
    else:
        padded_sequence = input_indices  # No need for padding or truncation
    return padded_sequence

# Define your input product IDs
input_product_ids_list = [[292]]  # Replace these with your actual product IDs
max_test_sequence_length = max(len(seq) for seq in sequences)  # Define the maximum length of the input sequence

# Example: Make predictions for the first 5 sequences in the test set
predictions = model.predict(np.array(input_product_ids_list))

# Convert predictions to their original form (product IDs)
for i, (sequence, pred) in enumerate(zip(input_product_ids_list, predictions)):
    next_item_index = np.argmax(pred[-1])  # Get the index of the next item with the highest probability
    next_item = unique_items[next_item_index]
    input_sequence = [unique_items[item_index] for item_index in sequence]
    print(f"Input Sequence: {input_sequence}, Predicted Next Item: {next_item}")

1/1 [==============================] - 0s 20ms/step
Input Sequence: [293], Predicted Next Item: 294


In [325]:
# Combine input_product_ids and next_items into sequence_to_check
sequence_to_check = input_sequence + next_item

In [326]:
# Group the DataFrame by 'order_id' and convert product ids in each group to a list
df_grouped = dfplus.groupby('order_id')['product_id'].apply(list)
df_grouped.head()

order_id
3181466                           [307, 2111, 277]
3181501                    [237, 2755, 1305, 2160]
3181506    [1104, 1102, 2816, 2461, 877, 878, 112]
3181509                                     [2630]
3181512                           [1157, 447, 546]
Name: product_id, dtype: object

In [327]:
# Define a function to check if the sequence_to_check is a subsequence of each transaction
def is_subsequence(transaction):
    it = iter(transaction)
    return all(item in it for item in sequence_to_check)

# Apply the function to each transaction in the grouped data
sequence_exists = df_grouped.apply(is_subsequence).any()

print(sequence_exists)

True


In [328]:
# Define a function to check if the sequence_to_check is a subsequence of each transaction
def is_subsequence(transaction):
    it = iter(transaction)
    return all(item in it for item in sequence_to_check)

# Apply the function to each transaction in the grouped data and sum the results
sequence_count = df_grouped.apply(is_subsequence).sum()

print(sequence_count)


114
